In [1]:
 
username ='liuweiwang0824@gmail.com'
password ='Umcqar45&M'
 
import random

import pytz
from datetime import timedelta
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime
import time as time_module
from robin_stocks.orders import order_sell_stop_loss
def login():
    rh.login(username, password)
def get_stop(stock):# pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = (today-datetime.timedelta(1)).strftime('%Y-%m-%d')
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{stock}?from={start}&to={end}&apikey={api_key}').json()['historical']
       
        # Print the raw data to check
        #print(f"Raw data for {stock}:")
       # print(bs)
       
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        last_day['center_gravity']=round(last_day['center_gravity'],2)
        # Print calculations
        #print("\nCalculations:")
      #  print(f"Center of Gravity: {last_day['center_gravity'].values[0]}")
       
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        last_day['vol_up1']=round(last_day['vol_up1'],2)
      #  print(f"Volatility Up 1: {last_day['vol_up1'].values[0]}")
       
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        last_day['vol_down1']=round(last_day['vol_down1'],2)
       # print(f"Volatility Down 1: {last_day['vol_down1'].values[0]}")
       
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        last_day['vol_up2']=round(last_day['vol_up2'],2)
      #  print(f"Volatility Up 2: {last_day['vol_up2'].values[0]}")
      #  
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        last_day['vol_down2']=round(last_day['vol_down2'],2)
       # print(f"Volatility Down 2: {last_day['vol_down2'].values[0]}")
       
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        last_day['vol_up3']=round(last_day['vol_up3'],2)
        #print(f"Volatility Up 3: {last_day['vol_up3'].values[0]}")
       
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        last_day['vol_down3']=round(last_day['vol_down3'],2)
        #print(f"Volatility Down 3: {last_day['vol_down3'].values[0]}")
       
        last_day['stop_loss'] = (last_day['vol_down2'] + last_day['vol_down3'])/2
        last_day['stop_loss']=round(last_day['stop_loss'],2)
        #print(f"Initial Stop Loss: {last_day['stop_loss'].values[0]}")
       
        last_day['stop_loss_pct'] = (last_day['Close'] - last_day['stop_loss'])/last_day['Close']*100
        last_day['stop_loss_pct']=round(last_day['stop_loss_pct'],2)
       # print(f"Initial Stop Loss Percentage: {last_day['stop_loss_pct'].values[0]}%")
       
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] + last_day['Close'][-1])/2
           # print(f"Adjusted Stop Loss (because percentage > 3.5%): {last_day['stop_loss'].values[0]}")
       
        return last_day

from pandas.tseries.holiday import USFederalHolidayCalendar
from datetime import time as datetime_time
def open_market():
    # Check if today is a weekend or holiday
    today = datetime.now().date()
    cal = USFederalHolidayCalendar()
    holidays = cal.holidays(start=today, end=today)
   
    if today.weekday() >= 5 or today in holidays:
        return False

    # Check if the current time is within trading hours
    time_now = datetime.now().time()
    market_open = datetime_time(9,30,0) # 9:30AM
    market_close = datetime_time(15,59,0) # 3:59PM

    if time_now > market_open and time_now < market_close:
        return True
    else:
        return False
 
def get_trailing_stop_percentage(stock):
#    print(f"Entering get_trailing_stop_percentage for {stock}...")
    stop_price = get_stop(stock)['stop_loss'][0]
    stop_price=round(stop_price,2)
    current_price = all_data1['price'][stock]
    trailing_percentage = (current_price - stop_price) / current_price
   
    # Print statements for debugging
    print(f"\nStock: {stock}")
    print(f"Current Price: ${current_price}")
    print(f"Stop Price from get_stop(): ${stop_price}")
    print(f"Trailing Percentage (from difference): {trailing_percentage*100:.2f}%")
#    print(f"Exiting get_trailing_stop_percentage for {stock}...")
   
    return trailing_percentage * 0.2  # Use 20% of the calculated stop percentage

def cancel_all_orders():
    open_orders = rh.orders.get_all_open_stock_orders()
    if not open_orders:  # Check if open_orders is None or empty
        print("No open orders found.")
        return
    for order in open_orders:
        if order:  # Check if the order is not None
            try:
                rh.orders.cancel_stock_order(order['id'])
                # Wait for a random time between 5 and 10 seconds
                time_to_sleep1 = random.uniform(5, 10)
                time_module.sleep(time_to_sleep1)
            except Exception as e:
                print(f"Error canceling order for {order['id']}: {e}")
        else:
            print("Found a None order.")

login()

sold_half = set()  # Track stocks that we have sold half of

while True:
    # Check if the market is open
    if open_market():
        print("Market is open.")

       
        cancel_all_orders()
        my_stocks = rh.build_holdings()
        df = pd.DataFrame(my_stocks).T
        df1 = df[['price', 'quantity', 'average_buy_price', 'percent_change']]
        stock = df1.index.tolist()
        all_data = pd.DataFrame()
   
        for ticker in stock:
            try:
                last_day = get_stop(ticker)
                last_day.index = [ticker]  
                all_data = pd.concat([all_data, last_day], axis=0)
            except Exception as e:
                print(f"Error processing stock {ticker}: {e}")
                if hasattr(e, 'response') and hasattr(e.response, 'text'):
                    print(e.response.text)
   
   
        all_data = all_data[['stop_loss']]
        all_data1 = df1.merge(all_data, left_index=True, right_index=True)
        all_data1['price'] = all_data1['price'].astype(float)
        all_data1['pct_cha'] = ((all_data1['price'] - all_data1['stop_loss']) / all_data1['price']) * 100
   
        x = random.random()
        y = float((x + 5) / 100)
        z = float((10 - x) / 100)
        all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
        all_data1['target_price1'] = all_data1['average_buy_price'] * (1 + y)
        all_data1['target_price1']=round(all_data1['target_price1'],2)
        all_data1['target_price2'] = all_data1['average_buy_price'] * (1 + z)
        all_data1['target_price2']=round(all_data1['target_price2'],2)
    #    print(all_data1)
   
        print("Starting the loop to process each stock for trailing stop...")

   
        for s in all_data1.index.tolist():
            current_price = all_data1['price'][s]
            average_price = all_data1['average_buy_price'][s]
            quantity = float(all_data1['quantity'][s])
            quantity0 = round(quantity, 4)
            quantity_to_sell=math.floor(quantity)
   
            trailing_stop_pct = get_trailing_stop_percentage(s)
            trailing_stop_price = current_price * (1 - trailing_stop_pct)
            loss_pct = (current_price - trailing_stop_price) / current_price * 100
            gain_pct = (current_price - average_price) / average_price * 100
   
            if all_data1['target_price1'][s] >= current_price:
                stopPrice_value = float(all_data1['stop_loss'][s])
                stopPrice_value = round(stopPrice_value, 2)
                limitPrice_value = stopPrice_value - 0.5  # 设置限价为“停止价格减去0.5”
                print(f"Symbol: {s}, Quantity: {quantity}, Stop Price: {stopPrice_value}, Limit Price: {limitPrice_value}")
            
                if quantity_to_sell >= 1:  # 添加这行检查
                    try:
                        response = rh.order(symbol=s, side='sell', stopPrice=str(stopPrice_value), limitPrice=str(limitPrice_value), quantity=str(quantity_to_sell), timeInForce='gtc')                
                        time_to_sleep = random.uniform(15, 30)
                        time_module.sleep(time_to_sleep)
                    except Exception as e:
                        print(f"Error executing order for {s}: {e}")
                        if hasattr(e, 'response'):
                            print("Error response:", e.response.text)
                            if hasattr(e.response, 'json'):
                                try:
                                    error_json = e.response.json()
                                    print("Error JSON:", error_json)
                                except:
                                    pass
                else:
                    print(f"Skipping order for {s} because quantity to sell is less than 1.")  # 添加这行输出
            
                print(f"First target price not yet reached for {s}, setting stop loss order.")
                print(f"Current Price: ${current_price:.2f}, Target Price 1: ${all_data1['target_price1'][s]:.2f}")
            
               
            elif current_price >= all_data1['target_price1'][s] and s not in sold_half:
                    if quantity0 >= 2:
                            quantity1 = math.ceil(quantity0 / 2)  # sell half
                            quantity1 = math.floor(quantity1)
                            try:
                                response = rh.orders.order_sell_market(symbol=s, quantity=quantity1, timeInForce='gfd')
                                time_to_sleep = random.uniform(15, 30)
                                time_module.sleep(time_to_sleep)
                            except Exception as e:
                                print(f"Error executing order for {s}: {e}")
                                if hasattr(e, 'response'):
                                    print("Error response:", e.response.text)
                                    if hasattr(e.response, 'json'):
                                        try:
                                            error_json = e.response.json()
                                            print("Error JSON:", error_json)
                                        except:
                                            pass
                            print(f"First target price reached for {s}, setting stop loss order for half at ${trailing_stop_price:.2f}.")
                            print(f"Current Price: ${current_price:.2f}, Target Price 1: ${all_data1['target_price1'][s]:.2f}")
                            sold_half.add(s)  # Add the stock to the sold half set
   
                    else:
                            try:
                                response = rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
                                time_to_sleep = random.uniform(15, 30)
                                time_module.sleep(time_to_sleep)
                            except Exception as e:
                                print(f"Error executing order for {s}: {e}")
                                if hasattr(e, 'response'):
                                    print("Error response:", e.response.text)
                                    if hasattr(e.response, 'json'):
                                        try:
                                            error_json = e.response.json()
                                            print("Error JSON:", error_json)
                                        except:
                                            pass
                            print(f"First target price reached for {s}, Current Price: ${current_price:.2f}, with a gain of {gain_pct:.2f}%.")
                            print(f"Due to low initial funding, the entire position in this stock has been sold for profit.")
   
   
            elif current_price >= all_data1['target_price2'][s]:    
                if quantity > 1:
                    sell_amount = math.floor(quantity)
                    try:
                        response = rh.order(symbol=s, side='sell', stopPrice=str(trailing_stop_price), limitPrice=str(trailing_stop_price-0.2), quantity=str(sell_amount), timeInForce='gtc')
                        time_to_sleep = random.uniform(15, 30)
                        time_module.sleep(time_to_sleep)
                    except Exception as e:
                        print(f"Error executing order for {s}: {e}")
                        if hasattr(e, 'response'):
                            print("Error response:", e.response.text)
                            if hasattr(e.response, 'json'):
                                try:
                                    error_json = e.response.json()
                                    print("Error JSON:", error_json)
                                except:
                                    pass
                    print(f"Second target price reached for {s}, setting stop loss order for all at ${trailing_stop_price:.2f} with a gain of {gain_pct:.2f}%.")
                    print(f"Current Price: ${current_price:.2f}, Target Price 2: ${all_data1['target_price2'][s]:.2f}, Average Buy Price: ${average_price:.2f}")
   
                else:
                    try:
                        response = rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
                        time_to_sleep = random.uniform(15, 30)
                        time_module.sleep(time_to_sleep)
                       
                    except Exception as e:
                        print(f"Error executing order for {s}: {e}")
                        if hasattr(e, 'response'):
                            print("Error response:", e.response.text)
                            if hasattr(e.response, 'json'):
                                try:
                                    error_json = e.response.json()
                                    print("Error JSON:", error_json)
                                except:
                                    pass
                               
                    print(f"Second target price reached for {s}, Current Price: ${current_price:.2f} with a gain of {gain_pct:.2f}%.")
                    print(f"Due to low initial funding, the entire position in this stock has been sold for profit.")
   
   
   
   
            elif current_price <= trailing_stop_price:
                try:
                    response = rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
                    time_to_sleep = random.uniform(15, 30)

                    time_module.sleep(time_to_sleep)

                   
                except Exception as e:
                    print(f"Error executing order for {s}: {e}")
                    if hasattr(e, 'response'):
                        print("Error response:", e.response.text)
                        if hasattr(e.response, 'json'):
                            try:
                                error_json = e.response.json()
                                print("Error JSON:", error_json)
                            except:
                                pass
                           
                print(f"Trailing stop would be triggered for {s}, close for all at ${trailing_stop_price:.2f}. ")
                print(f"Current Price: ${current_price:.2f}, Trailing Stop Price: ${trailing_stop_price:.2f}")
   
        print("Ending main loop iteration...")
        time_module.sleep(7200)  # Wait for an hour before checking again

    # else:
    #     print("Market is closed. Waiting for an hour before checking again.")
    #     time_module.sleep(7200)  # Wait for an hour before checking again
           
    else:
       print("Market is closed or it's past 3:30 PM ET. Waiting until 10:00 AM ET to start again.")
       
       # Calculate the number of seconds to wait until 10:00 AM ET the next day
       current_datetime_eastern = datetime.now(pytz.timezone('US/Eastern'))
       next_start_time = current_datetime_eastern.replace(hour=10, minute=0, second=0, microsecond=0) + timedelta(days=1)
       wait_seconds = (next_start_time - current_datetime_eastern).seconds
       
       time_module.sleep(wait_seconds)

Market is open.
Found Additional pages.
Loading page 2 ...
Loading page 3 ...
Loading page 4 ...
Loading page 5 ...
Loading page 6 ...
Loading page 7 ...
Loading page 8 ...
Loading page 9 ...
Loading page 10 ...
Loading page 11 ...
Loading page 12 ...
Loading page 13 ...
Loading page 14 ...
Loading page 15 ...
Loading page 16 ...
Loading page 17 ...
Loading page 18 ...
Loading page 19 ...
Loading page 20 ...
Loading page 21 ...
Loading page 22 ...
Loading page 23 ...
Loading page 24 ...
Loading page 25 ...
Loading page 26 ...
Loading page 27 ...
Loading page 28 ...
Loading page 29 ...
Loading page 30 ...
Loading page 31 ...
Loading page 32 ...
Loading page 33 ...
Loading page 34 ...
Loading page 35 ...
Loading page 36 ...
Loading page 37 ...
Loading page 38 ...
Loading page 39 ...
Loading page 40 ...
Loading page 41 ...
Loading page 42 ...
Loading page 43 ...
Loading page 44 ...
Loading page 45 ...
Loading page 46 ...
Loading page 47 ...
Loading page 48 ...
Loading page 49 ...
Loading 


Stock: GKOS
Current Price: $87.77
Stop Price from get_stop(): $88.44
Trailing Percentage (from difference): -0.76%
First target price reached for GKOS, setting stop loss order for half at $87.90.
Current Price: $87.77, Target Price 1: $86.51

Stock: TOL
Current Price: $98.655
Stop Price from get_stop(): $97.62
Trailing Percentage (from difference): 1.05%
Symbol: TOL, Quantity: 3.43, Stop Price: 97.62, Limit Price: 97.12
First target price not yet reached for TOL, setting stop loss order.
Current Price: $98.66, Target Price 1: $108.69

Stock: WSM
Current Price: $202.385
Stop Price from get_stop(): $196.32
Trailing Percentage (from difference): 3.00%
Symbol: WSM, Quantity: 1.77, Stop Price: 196.32, Limit Price: 195.82
First target price not yet reached for WSM, setting stop loss order.
Current Price: $202.38, Target Price 1: $210.33

Stock: XLF
Current Price: $37.32
Stop Price from get_stop(): $36.87
Trailing Percentage (from difference): 1.21%
Symbol: XLF, Quantity: 2.42, Stop Price: 3


Stock: ACGL
Current Price: $78.73
Stop Price from get_stop(): $76.5
Trailing Percentage (from difference): 2.83%
Symbol: ACGL, Quantity: 0.94, Stop Price: 76.5, Limit Price: 76.0
Skipping order for ACGL because quantity to sell is less than 1.
First target price not yet reached for ACGL, setting stop loss order.
Current Price: $78.73, Target Price 1: $82.81

Stock: ETR
Current Price: $100.15
Stop Price from get_stop(): $100.52
Trailing Percentage (from difference): -0.37%
Symbol: ETR, Quantity: 0.35, Stop Price: 100.52, Limit Price: 100.02
Skipping order for ETR because quantity to sell is less than 1.
First target price not yet reached for ETR, setting stop loss order.
Current Price: $100.15, Target Price 1: $110.07

Stock: EGP
Current Price: $176.4
Stop Price from get_stop(): $174.76
Trailing Percentage (from difference): 0.93%
Symbol: EGP, Quantity: 0.93, Stop Price: 174.76, Limit Price: 174.26
Skipping order for EGP because quantity to sell is less than 1.
First target price not y


Stock: EA
Current Price: $136.46
Stop Price from get_stop(): $134.78
Trailing Percentage (from difference): 1.23%
Symbol: EA, Quantity: 0.33, Stop Price: 134.78, Limit Price: 134.28
Skipping order for EA because quantity to sell is less than 1.
First target price not yet reached for EA, setting stop loss order.
Current Price: $136.46, Target Price 1: $146.66

Stock: CMS
Current Price: $57.13
Stop Price from get_stop(): $56.94
Trailing Percentage (from difference): 0.33%
Symbol: CMS, Quantity: 0.01, Stop Price: 56.94, Limit Price: 56.44
Skipping order for CMS because quantity to sell is less than 1.
First target price not yet reached for CMS, setting stop loss order.
Current Price: $57.13, Target Price 1: $63.19

Stock: ETN
Current Price: $237.095
Stop Price from get_stop(): $235.32
Trailing Percentage (from difference): 0.75%
Symbol: ETN, Quantity: 0.59, Stop Price: 235.32, Limit Price: 234.82
Skipping order for ETN because quantity to sell is less than 1.
First target price not yet r

Order 65a82ea1-703a-49bb-bc32-9a57bc8abedc cancelled
Order 65a82e90-dee9-4c4c-80cc-83be4faf06c3 cancelled
Starting the loop to process each stock for trailing stop...

Stock: META
Current Price: $372.485
Stop Price from get_stop(): $365.08
Trailing Percentage (from difference): 1.99%
Symbol: META, Quantity: 0.8494, Stop Price: 365.09, Limit Price: 364.59
Skipping order for META because quantity to sell is less than 1.
First target price not yet reached for META, setting stop loss order.
Current Price: $372.49, Target Price 1: $386.02

Stock: TTWO
Current Price: $160.28
Stop Price from get_stop(): $156.05
Trailing Percentage (from difference): 2.64%
Symbol: TTWO, Quantity: 0.01, Stop Price: 156.05, Limit Price: 155.55
Skipping order for TTWO because quantity to sell is less than 1.
First target price not yet reached for TTWO, setting stop loss order.
Current Price: $160.28, Target Price 1: $169.32

Stock: MU
Current Price: $85.525
Stop Price from get_stop(): $81.27
Trailing Percentage (

...

Loading page 16 ...
Loading page 17 ...
Loading page 18 ...
Loading page 19 ...
Loading page 20 ...
Loading page 21 ...
Loading page 22 ...
Loading page 23 ...
Loading page 24 ...
Loading page 25 ...
Loading page 26 ...
Loading page 27 ...
Loading page 28 ...
Loading page 29 ...
Loading page 30 ...
Loading page 31 ...
Loading page 32 ...
Loading page 33 ...
Loading page 34 ...
Loading page 35 ...
Loading page 36 ...
Loading page 37 ...
Loading page 38 ...
Loading page 39 ...
Loading page 40 ...
Loading page 41 ...
Loading page 42 ...
Loading page 43 ...
Loading page 44 ...
Loading page 45 ...
Loading page 46 ...
Loading page 47 ...
Loading page 48 ...
Loading page 49 ...
Loading page 50 ...
Loading page 51 ...
Loading page 52 ...
Loading page 53 ...
Loading page 54 ...
Loading page 55 ...
Loading page 56 ...
Loading page 57 ...
Loading page 58 ...
Loading page 59 ...
Loading page 60 ...
Loading page 61 ...
Loading page 62 ...
Loading page 63 ...
Loading page 64 ...
Loading page 65 ...


First target price not yet reached for CNXC, setting stop loss order.
Current Price: $102.89, Target Price 1: $108.42

Stock: EA
Current Price: $138.625
Stop Price from get_stop(): $136.17
Trailing Percentage (from difference): 1.77%
Symbol: EA, Quantity: 0.33, Stop Price: 136.17, Limit Price: 135.67
Skipping order for EA because quantity to sell is less than 1.
First target price not yet reached for EA, setting stop loss order.
Current Price: $138.62, Target Price 1: $145.55

Stock: DDOG
Current Price: $130.65
Stop Price from get_stop(): $132.07
Trailing Percentage (from difference): -1.09%
Symbol: DDOG, Quantity: 4.35, Stop Price: 132.07, Limit Price: 131.57
First target price not yet reached for DDOG, setting stop loss order.
Current Price: $130.65, Target Price 1: $135.23

Stock: CMS
Current Price: $56.645
Stop Price from get_stop(): $55.46
Trailing Percentage (from difference): 2.09%
Symbol: CMS, Quantity: 0.01, Stop Price: 55.46, Limit Price: 54.96
Skipping order for CMS because 

First target price not yet reached for WDAY, setting stop loss order.
Current Price: $289.37, Target Price 1: $302.31

Stock: STT
Current Price: $74.05
Stop Price from get_stop(): $73.84
Trailing Percentage (from difference): 0.28%
Symbol: STT, Quantity: 0.21, Stop Price: 73.84, Limit Price: 73.34
Skipping order for STT because quantity to sell is less than 1.
First target price not yet reached for STT, setting stop loss order.
Current Price: $74.05, Target Price 1: $81.53

Stock: SRE
Current Price: $71.68
Stop Price from get_stop(): $69.3
Trailing Percentage (from difference): 3.32%
Symbol: SRE, Quantity: 0.28, Stop Price: 69.3, Limit Price: 68.8
Skipping order for SRE because quantity to sell is less than 1.
First target price not yet reached for SRE, setting stop loss order.
Current Price: $71.68, Target Price 1: $80.35

Stock: GRMN
Current Price: $126.28
Stop Price from get_stop(): $124.74
Trailing Percentage (from difference): 1.22%
Symbol: GRMN, Quantity: 4.47, Stop Price: 124.74

First target price not yet reached for HRI, setting stop loss order.
Current Price: $145.23, Target Price 1: $154.34

Stock: KAI
Current Price: $277.225
Stop Price from get_stop(): $275.36
Trailing Percentage (from difference): 0.67%
Symbol: KAI, Quantity: 0.8194, Stop Price: 275.37, Limit Price: 274.87
Skipping order for KAI because quantity to sell is less than 1.
First target price not yet reached for KAI, setting stop loss order.
Current Price: $277.23, Target Price 1: $290.68

Stock: MTD
Current Price: $1212.42
Stop Price from get_stop(): $1187.63
Trailing Percentage (from difference): 2.04%
Symbol: MTD, Quantity: 0.1876, Stop Price: 1187.63, Limit Price: 1187.13
Skipping order for MTD because quantity to sell is less than 1.
First target price not yet reached for MTD, setting stop loss order.
Current Price: $1212.42, Target Price 1: $1269.60

Stock: OZK
Current Price: $49.57
Stop Price from get_stop(): $48.86
Trailing Percentage (from difference): 1.43%
Symbol: OZK, Quantity: 4.6

TypeError: 'NoneType' object is not subscriptable